In [6]:
#Read the 0.dat file
text = ""
for fname in ["0.dat", "1.dat", "2.dat", "3.dat"]:
    with open(fname, "r") as fp:
        text += " " + fp.read()

In [9]:
docs = text.split("##")
docs

[' 0|ETFs   Smart Portfolio   Currencies   Online Broker Center\nTomorrow is a market of endless possibilities  learn more\n  Quotes   Research Flash Quotes InfoQuotes Summary Quotes Real time Quotes Extended Trading Options Trading Center Historical Quotes\n  Companies Company News Press Releases Company List Nasdaq Companies\n  Stock Analysis Analyst Research Guru Analysis Stock Reports Competitors\n  Fundamentals Financials Revenue EPS SEC Filings Short Interest Dividend History\n  Holdings Ownership Summary Institutional Holdings Insiders Form  \n  Extended Hours Pre Market Activity After Hours Activity\n  Stocks Most Active Unusual Volume    Week High Low Upcoming Splits New SEC Filings IPO Summary Earnings Calendar Dividend Stocks Sector Analysis\n  Analyst Activity Upgrades Downgrades Forecast Changes Earning Surprises\n  Indices Major Stock Indices Market Sector Indices Statistical Milestones\nIntel and Alibaba Team Up in the AI  IoT  and Cloud Markets\nHow data is making the U

In [22]:
doc_id_to_doc = {}
for doc in docs:
    split_by_bar = doc.strip().split("|")
    try:
        id, doc_text = split_by_bar
    except Exception as e:
        id, doc_text = split_by_bar[0], ' '.join(split_by_bar[1:])
    if doc_text != '':
        doc_id_to_doc.update({
            id: doc_text.lower()
        })

In [25]:
doc_id_to_doc.values()

['king signs deal with skybrands to launch a line of clothing based on the popular game \n  casual games company king has signed a european licensing deal with apparel specialist skybrands for its popular property candy crush saga \nskybrands will aim to incorporate the essence of the game within a range of clothing featuring the brand s logo  sweets and characters \ncandy crush saga   released by king in april        now reaches over    million fans of facebook and was crowned the number one free app of last year \ngilles storme  senior director licensing at king  said   candy crush saga fans all over europe will be thrilled at the opportunity to wear clothing inspired by their favourite game \n we re delighted to have signed this apparel deal with one of the fastest growing and respected names in the business \n with skybrands  global sourcing capabilities and deep retail relationships  we can fulfi are disappointed the city has chosen to bring this action  which we strongly believe 

In [42]:
bad_article_phrases = ["you must be a digital subscriber to view this article", 
                "nothing was found at this location",
                "the page you are looking for has either been moved",
                "your usage has been flagged as a violation of our terms of service",
                "you don t have permission to acces",
                "this page seems to have disappeared through a portal",
                "subscribe today for full access on your desktop  tablet",
                "the requested document was not found on this server",
                "has banned your access based on your browser s signature",
                "has banned your access based on your browser's signature",
                "the link you followed no longer exists",
                "the server can not find the requested page"]

In [43]:
#refactoring the docs.
bad_docs = []
for id, doc in doc_id_to_doc.iteritems():
    for bad_article_phrase in bad_article_phrases:
        if bad_article_phrase in doc:
            bad_docs.append(id)
            continue

In [44]:
print(len(bad_docs))
#filter the docs
for id in bad_docs:
    doc_id_to_doc.pop(id, None)

392


In [45]:
doc_id_to_doc.values()

['king signs deal with skybrands to launch a line of clothing based on the popular game \n  casual games company king has signed a european licensing deal with apparel specialist skybrands for its popular property candy crush saga \nskybrands will aim to incorporate the essence of the game within a range of clothing featuring the brand s logo  sweets and characters \ncandy crush saga   released by king in april        now reaches over    million fans of facebook and was crowned the number one free app of last year \ngilles storme  senior director licensing at king  said   candy crush saga fans all over europe will be thrilled at the opportunity to wear clothing inspired by their favourite game \n we re delighted to have signed this apparel deal with one of the fastest growing and respected names in the business \n with skybrands  global sourcing capabilities and deep retail relationships  we can fulfi are disappointed the city has chosen to bring this action  which we strongly believe 

In [46]:
#Replace \n with tabs
for id in doc_id_to_doc:
    doc_id_to_doc[id] = doc_id_to_doc[id].replace("\n", " ").strip()

In [47]:
import gensim

/usr/local/lib/python2.7/dist-packages/scipy/sparse/lil.py:19: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from . import _csparsetools
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/__init__.py:165: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from ._shortest_path import shortest_path, floyd_warshall, dijkstra,\
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/_validation.py:5: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from ._tools import csgraph_to_dense, csgraph_from_dense,\
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/__init__.py:167: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  from ._traversal import breadth_first_order, depth_first_order, \
/usr/local/lib/python2.7/dist-packages/scipy/sparse/csgraph/__init__.py:169: R

In [50]:
#Lets try the preprocessing module
doc_to_preprocessed_text = {}
for id, doc in doc_id_to_doc.iteritems():
    doc_to_preprocessed_text[id] = gensim.utils.simple_preprocess(doc)

In [51]:
documents = doc_to_preprocessed_text.values()
model = gensim.models.Word2Vec(documents,
        size=200,
        window=10,
        min_count=2,
        workers=10)
model.train(documents, total_examples=len(documents), epochs=10)


(14987908, 17931250)

In [52]:
model.wv.most_similar("news")

[(u'breaking', 0.8807220458984375),
 (u'itpro', 0.7821805477142334),
 (u'newsletter', 0.7775389552116394),
 (u'bloombergtv', 0.7664504051208496),
 (u'daily', 0.7547646164894104),
 (u'headlines', 0.7478547096252441),
 (u'journal', 0.7428438067436218),
 (u'authoritative', 0.7426567077636719),
 (u'latest', 0.7417762875556946),
 (u'npr', 0.7395294308662415)]